In [2]:
# Installing the necessary dependencies
!pip install -q ipywidgets openpyxl

import pandas as pd
import ipywidgets as widgets
from IPython.display import display,HTML,clear_output
from io import BytesIO
import base64
import re
import requests, base64
from IPython.display import display
import ipywidgets as widgets

# --------------------------
# Fetched & Embedded the Banner
# --------------------------

DRIVE_ID="1En-wAZgn3SSR1ZD1ZA6Ld1EJuAYQ4aAL"
GDRIVE_URL=f"https://drive.google.com/uc?export=download&id={DRIVE_ID}"
resp=requests.get(GDRIVE_URL)
b64_png=base64.b64encode(resp.content).decode()
banner= widgets.HTML(
    value=f"""
    <div style="text-align:center; margin-bottom:10px;">
      <img src="data:image/png;base64,{b64_png}"
           alt="Banner" style="max-width:50%; height:auto;"/>
    </div>
    """
)


# --------------------------
# Defining the Institute Groups
# --------------------------

IITs={'Indian Institute of Technology Bhubaneswar',
      'Indian Institute of Technology Bombay',
      'Indian Institute of Technology Mandi',
      'Indian Institute of Technology Delhi',
      'Indian Institute of Technology Indore',
      'Indian Institute of Technology Kharagpur',
      'Indian Institute of Technology Hyderabad',
      'Indian Institute of Technology Jodhpur',
      'Indian Institute of Technology Kanpur',
      'Indian Institute of Technology Madras',
      'Indian Institute of Technology Gandhinagar',
      'Indian Institute of Technology Patna',
      'Indian Institute of Technology Roorkee',
      'Indian Institute of Technology (ISM) Dhanbad',
      'Indian Institute of Technology Ropar',
      'Indian Institute of Technology (BHU) Varanasi',
      'Indian Institute of Technology Guwahati',
      'Indian Institute of Technology Bhilai',
      'Indian Institute of Technology Goa',
      'Indian Institute of Technology Palakkad',
      'Indian Institute of Technology Tirupati',
      'Indian Institute of Technology Jammu',
      'Indian Institute of Technology Dharwad'}

NITs={'Dr. B R Ambedkar National Institute of Technology, Jalandhar',
      'Malaviya National Institute of Technology Jaipur',
      'Maulana Azad National Institute of Technology Bhopal',
      'Motilal Nehru National Institute of Technology Allahabad',
      'National Institute of Technology Agartala',
      'National Institute of Technology Calicut',
      'National Institute of Technology Delhi',
      'National Institute of Technology Durgapur',
      'National Institute of Technology Goa',
      'National Institute of Technology Hamirpur',
      'National Institute of Technology Karnataka, Surathkal',
      'National Institute of Technology Meghalaya',
      'National Institute of Technology Nagaland',
      'National Institute of Technology Patna',
      'National Institute of Technology Puducherry',
      'National Institute of Technology Raipur',
      'National Institute of Technology Sikkim',
      'National Institute of Technology Arunachal Pradesh',
      'National Institute of Technology, Jamshedpur',
      'National Institute of Technology, Kurukshetra',
      'National Institute of Technology, Manipur',
      'National Institute of Technology, Mizoram',
      'National Institute of Technology, Rourkela',
      'National Institute of Technology, Silchar',
      'National Institute of Technology, Srinagar',
      'National Institute of Technology, Tiruchirappalli',
      'National Institute of Technology, Uttarakhand',
      'National Institute of Technology, Warangal',
      'Sardar Vallabhbhai National Institute of Technology, Surat',
      'Visvesvaraya National Institute of Technology, Nagpur',
      'National Institute of Technology, Andhra Pradesh',
      'Indian Institute of Engineering Science and Technology, Shibpur'}

IIITs={'Atal Bihari Vajpayee Indian Institute of Information Technology & Management Gwalior',
       'Indian Institute of Information Technology (IIIT)Kota, Rajasthan',
       'Indian Institute of Information Technology Guwahati',
       'Indian Institute of Information Technology(IIIT) Kalyani, West Bengal',
       'Indian Institute of Information Technology(IIIT) Kilohrad, Sonepat, Haryana',
       'Indian Institute of Information Technology(IIIT) Una, Himachal Pradesh',
       'Indian Institute of Information Technology (IIIT), Sri City, Chittoor',
       'Indian Institute of Information Technology(IIIT), Vadodara, Gujrat',
       'Indian Institute of Information Technology, Allahabad',
       'Indian Institute of Information Technology, Design & Manufacturing, Kancheepuram',
       'Pt. Dwarka Prasad Mishra Indian Institute of Information Technology, Design & Manufacture Jabalpur',
       'INDIAN INSTITUTE OF INFORMATION TECHNOLOGY SENAPATI MANIPUR',
       'Indian Institute of Information Technology Tiruchirappalli',
       'Indian Institute of Information Technology Lucknow',
       'Indian Institute of Information Technology(IIIT) Dharwad',
       'Indian Institute of Information Technology Design & Manufacturing Kurnool, Andhra Pradesh',
       'Indian Institute of Information Technology(IIIT) Kottayam',
       'Indian Institute of Information Technology (IIIT) Ranchi',
       'Indian Institute of Information Technology (IIIT) Nagpur',
       'Indian Institute of Information Technology (IIIT) Pune',
       'Indian Institute of Information Technology Bhagalpur',
       'Indian Institute of Information Technology Bhopal',
       'Indian Institute of Information Technology Surat',
       'Indian Institute of Information Technology, Agartala',
       'Indian institute of information technology, Raichur, Karnataka',
       'Indian Institute of Information Technology, Vadodara International Campus Diu (IIITVICD)'}

ALL_INSTITUTES=IITs.union(NITs).union(IIITs)

# --------------------------
# Loading the data as an Excel File
# --------------------------

file_path='/content/Josaa Data.xlsx'
xls=pd.ExcelFile(file_path)
sheet_names=xls.sheet_names

year_rounds={}
for name in sheet_names:
    m=re.match(r'(\d{4})_R(\d+)',name)
    if m:
        yr,rnd=m.groups()
        year_rounds.setdefault(yr,[]).append(int(rnd))
for yr in year_rounds:
    year_rounds[yr].sort()

years=sorted(year_rounds.keys(),reverse=True)
year_dropdown=widgets.Dropdown(options=years,description='Year:')
round_dropdown=widgets.Dropdown(description='Round:')

def update_rounds(chg):
    round_dropdown.options=year_rounds[chg['new']]
year_dropdown.observe(update_rounds,names='value')
update_rounds({'new':year_dropdown.value})

def load_sheet_df(yr,rnd):
    df=pd.read_excel(xls,sheet_name=f"{yr}_R{rnd}")
    return df.rename(columns=lambda c:c.strip())

df_sample=load_sheet_df(years[0],year_rounds[years[0]][0])
programs=df_sample['Academic Program Name'].dropna().unique().tolist()
five_year_keywords=['5 Years','Dual Degree','Integrated','B.S.-M.S.','B.Tech-M.Tech']
five_year_programs={p for p in programs if any(k.lower() in p.lower() for k in five_year_keywords)}

# --------------------------
# Defining the Widgets
# --------------------------

note_html       = widgets.HTML("<b>Note:</b> If you haven’t cleared JEE&nbsp;Mains or JEE&nbsp;Advanced, please enter the rank as <b>0</b>.")
jee_main_input  = widgets.IntText(description="JEE Mains:",value=1500000)
jee_adv_input   = widgets.IntText(description="JEE Adv:",value=400000)
inst_dropdown   = widgets.Dropdown(description='Institute:')
gender_dropdown = widgets.Dropdown(description='Gender:')
seat_dropdown   = widgets.Dropdown(description='Seat Type:')
course_duration = widgets.ToggleButtons(options=['4-Year','5-Year','Both'],value='Both',description='Duration:')
buffer_input    = widgets.BoundedIntText(description='Rank Buffer:',value=700,min=0,max=10000)
submit_btn      = widgets.Button(description="Show Results",button_style='success')
advanced_btn    = widgets.ToggleButton(value=False,description='Advanced Filters',button_style='info')
refresh_btn     = widgets.Button(description='🔄 Refresh All',button_style='warning')
output_area     = widgets.Output()

# --------------------------
# Defining the Advanced Filters
# --------------------------

def create_scrollable_vbox(checkboxes):
    return widgets.Box(
        [widgets.VBox(checkboxes)],
        layout=widgets.Layout(overflow='auto',max_height='200px',width='auto',
                              border='1px solid gray',padding='5px',
                              display='flex',flex_flow='column nowrap')
    )

iit_checkboxes=[widgets.Checkbox(value=True,description=inst) for inst in sorted(IITs)]
for cb in iit_checkboxes:
    cb.layout.width='600px'
nit_checkboxes=[widgets.Checkbox(value=True,description=inst) for inst in sorted(NITs)]
for cb in nit_checkboxes:
    cb.layout.width='600px'
iiit_checkboxes=[widgets.Checkbox(value=True,description=inst) for inst in sorted(IIITs)]
for cb in iiit_checkboxes:
    cb.layout.width='600px'
all_institutes_in_excel=set(df_sample['Institute'].unique())
GFTIs=all_institutes_in_excel-ALL_INSTITUTES
gfti_checkboxes=[widgets.Checkbox(value=True,description=inst) for inst in sorted(GFTIs)]
for cb in gfti_checkboxes:
    cb.layout.width='600px'

checkbox_groups={
    'IITs': create_scrollable_vbox(iit_checkboxes),
    'NITs': create_scrollable_vbox(nit_checkboxes),
    'IIITs': create_scrollable_vbox(iiit_checkboxes),
    'GFTIs': create_scrollable_vbox(gfti_checkboxes),
    'ALL': widgets.VBox([
        widgets.Label("IITs:"),create_scrollable_vbox(iit_checkboxes),
        widgets.Label("NITs:"),create_scrollable_vbox(nit_checkboxes),
        widgets.Label("IIITs:"),create_scrollable_vbox(iiit_checkboxes),
        widgets.Label("GFTIs:"),create_scrollable_vbox(gfti_checkboxes),
    ])
}

inst_checkbox_map={
    'IITs': iit_checkboxes,
    'NITs': nit_checkboxes,
    'IIITs': iiit_checkboxes,
    'GFTIs': gfti_checkboxes,
    'ALL': iit_checkboxes + nit_checkboxes + iiit_checkboxes + gfti_checkboxes
}

inst_checkboxes_container=widgets.VBox()

# Select/Deselect All Buttons

def set_all_checkboxes(state=True):
    cbs=inst_checkbox_map.get(inst_dropdown.value,[])
    for cb in cbs:
        cb.unobserve(on_inst_checkbox_changed,names='value')
    for cb in cbs:
        cb.value=state
    for cb in cbs:
        cb.observe(on_inst_checkbox_changed,names='value')
    update_program_checkboxes()

select_all_btn=widgets.Button(description='✅ Select All',button_style='primary')
deselect_all_btn=widgets.Button(description='❌ Deselect All',button_style='danger')
select_all_btn.on_click(lambda _:set_all_checkboxes(True))
deselect_all_btn.on_click(lambda _:set_all_checkboxes(False))

# --------------------------
# Advanced Filters - Programs
# --------------------------

program_checkboxes=[]
program_box_container=widgets.VBox()

def update_program_checkboxes(*_):
    yr,rnd=year_dropdown.value,round_dropdown.value
    df=load_sheet_df(yr,rnd)
    df=df[pd.to_numeric(df['Opening Rank'],errors='coerce').notnull()]
    df=df[pd.to_numeric(df['Closing Rank'],errors='coerce').notnull()]
    df[['Opening Rank','Closing Rank']]=df[['Opening Rank','Closing Rank']].astype(int)

    cbs=inst_checkbox_map.get(inst_dropdown.value,[])
    selected_insts={cb.description for cb in cbs if cb.value}
    df=df[df['Institute'].isin(selected_insts)]

    if course_duration.value=='4-Year':
        df=df[~df['Academic Program Name'].isin(five_year_programs)]
    elif course_duration.value=='5-Year':
        df=df[df['Academic Program Name'].isin(five_year_programs)]
    if gender_dropdown.value:
        df=df[df['Gender']==gender_dropdown.value]
    if seat_dropdown.value:
        df=df[df['Seat Type']==seat_dropdown.value]

    prog_list=sorted(df['Academic Program Name'].dropna().unique())
    program_checkboxes.clear()
    for prog in prog_list:
        program_checkboxes.append(widgets.Checkbox(value=True,description=prog,layout=widgets.Layout(width='600px')))
    program_box_container.children=[create_scrollable_vbox(program_checkboxes)]

def set_all_programs(state=True):
    for cb in program_checkboxes:
        cb.value=state

select_all_prog_btn=widgets.Button(description='✅ Select All',button_style='primary')
deselect_all_prog_btn=widgets.Button(description='❌ Deselect All',button_style='danger')
select_all_prog_btn.on_click(lambda _:set_all_programs(True))
deselect_all_prog_btn.on_click(lambda _:set_all_programs(False))

# --------------------------
# Hooking up the Institute checkbox observer
# --------------------------

def on_inst_checkbox_changed(change):
    update_program_checkboxes()

for group in inst_checkbox_map.values():
    for cb in group:
        cb.observe(on_inst_checkbox_changed,names='value')

# also rebuild on any top‐level filter change
for w in [year_dropdown,round_dropdown,course_duration,gender_dropdown,seat_dropdown]:
    w.observe(update_program_checkboxes,names='value')

update_program_checkboxes()

# --------------------------
# Advanced Filter Container
# --------------------------

advanced_filter_box=widgets.VBox([
    widgets.Label("✅ Select Institutes (Deselect to Exclude):"),
    inst_checkboxes_container,
    widgets.HBox([select_all_btn,deselect_all_btn]),
    widgets.HTML("<hr>"),
    widgets.Label("✅ Select Academic Programs:"),
    program_box_container,
    widgets.HBox([select_all_prog_btn,deselect_all_prog_btn]),
    widgets.HTML("<hr>"),
    buffer_input,
    widgets.HTML("<i>ℹ️ The <b>Rank Buffer</b> widens the eligible closing rank range by the specified value.</i>")
])

def update_advanced_filter(*_):
    sel=inst_dropdown.value
    inst_checkboxes_container.children=[checkbox_groups[sel]] if sel in checkbox_groups else []

inst_dropdown.observe(update_advanced_filter,names='value')
adv_box=widgets.VBox([advanced_filter_box])
adv_box.layout.display='none'
advanced_btn.observe(lambda ch: adv_box.layout.__setattr__('display', 'block' if ch['new'] else 'none'),names='value')

# --------------------------
# Dynamic Filter Interconnection
# --------------------------

def update_filters(*_):
    df=load_sheet_df(year_dropdown.value,round_dropdown.value)
    if course_duration.value=='4-Year':
        df=df[~df['Academic Program Name'].isin(five_year_programs)]
    elif course_duration.value=='5-Year':
        df=df[df['Academic Program Name'].isin(five_year_programs)]
    df=df[pd.to_numeric(df['Opening Rank'],errors='coerce').notnull()]
    gender_dropdown.options=df['Gender'].dropna().unique().tolist()
    seat_dropdown.options=df['Seat Type'].dropna().unique().tolist()
    update_program_checkboxes()

for w in [course_duration,year_dropdown,round_dropdown]:
    w.observe(update_filters,names='value')
update_filters()

# --------------------------
# Institute dropdown logic
# --------------------------

def refresh_institute_list(*_):
    jm,ja=jee_main_input.value,jee_adv_input.value
    opts=[]
    if jm>0:
        opts+=["NITs","IIITs","GFTIs"]
        if ja>0:
            opts.insert(0,"IITs")
            opts.insert(0,"ALL")
    inst_dropdown.options=opts or ["-- Not Eligible --"]
    update_advanced_filter()

jee_main_input.observe(refresh_institute_list,names='value')
jee_adv_input.observe(refresh_institute_list,names='value')
refresh_institute_list()

# --------------------------
# Reset & Show Results
# --------------------------

def reset_all(_=None):
    jee_main_input.value = 1500000
    jee_adv_input.value  = 400000
    year_dropdown.value  = years[0]
    round_dropdown.value = year_rounds[years[0]][0]
    course_duration.value= 'Both'
    buffer_input.value   = 700
    set_all_checkboxes(True)
    set_all_programs(True)
    refresh_institute_list()
    update_filters()
    inst_dropdown.value  = inst_dropdown.options[0] if inst_dropdown.options else None
    update_advanced_filter()

refresh_btn.on_click(reset_all)

def show_results(_):
    with output_area:
        clear_output()
        jm, ja = jee_main_input.value, jee_adv_input.value
        yr, rnd = year_dropdown.value, round_dropdown.value
        sheet = f"{yr}_R{rnd}"
        inst_type = inst_dropdown.value
        gender, seat = gender_dropdown.value, seat_dropdown.value
        duration, buffer = course_duration.value, buffer_input.value

        if sheet not in sheet_names:
            print(f"❌ Sheet '{sheet}' not found."); return

        df = load_sheet_df(yr, rnd)
        df = df[pd.to_numeric(df['Opening Rank'], errors='coerce').notnull()]
        df = df[pd.to_numeric(df['Closing Rank'], errors='coerce').notnull()]
        df[['Opening Rank','Closing Rank']] = df[['Opening Rank','Closing Rank']].astype(int)

        if inst_type=="IITs":
            if jm==0 or ja==0: print("❌ Must clear both JEE exams."); return
            user_rank, inst_set = ja, IITs
        elif inst_type=="NITs":
            if jm==0: print("❌ Must clear JEE Mains."); return
            user_rank, inst_set = jm, NITs
        elif inst_type=="IIITs":
            if jm==0: print("❌ Must clear JEE Mains."); return
            user_rank, inst_set = jm, IIITs
        elif inst_type=="GFTIs":
            if jm==0: print("❌ Must clear JEE Mains."); return
            user_rank, inst_set = jm, GFTIs
        else:  # ALL
            if jm==0 or ja==0: print("❌ Must clear both JEE exams."); return
            user_rank, inst_set = min(jm,ja), all_institutes_in_excel

        # Applying advanced‐filter for institutes & programs
        chosen_insts = {cb.description for cb in inst_checkbox_map.get(inst_type, []) if cb.value}
        inst_set &= chosen_insts
        chosen_progs = {cb.description for cb in program_checkboxes if cb.value}

        if duration=='4-Year':
            df = df[~df['Academic Program Name'].isin(five_year_programs)]
        elif duration=='5-Year':
            df = df[df['Academic Program Name'].isin(five_year_programs)]

        filt = df[
            df['Institute'].isin(inst_set) &
            df['Academic Program Name'].isin(chosen_progs) &
            (df['Gender']==gender) &
            (df['Seat Type']==seat) &
            (
                ((df['Opening Rank']<=user_rank) & (df['Closing Rank']+buffer>=user_rank))
                | (df['Opening Rank']>=(user_rank-buffer))
            )
        ][['Institute','Academic Program Name','Quota','Gender','Seat Type','Opening Rank','Closing Rank']
        ].sort_values('Opening Rank')

        if filt.empty:
            print("❌ No programs found.")
        else:
            print(f"✅ Programs for rank {user_rank} in {inst_type} "
                  f"(Gender: {gender}, Seat: {seat}, Duration: {duration})")
            buf = BytesIO(); filt.to_excel(buf, index=False); buf.seek(0)
            link = base64.b64encode(buf.read()).decode()
            display(HTML(f'<a download="results.xlsx" href="data:application/vnd.openxmlformats-officedocument.spreadsheetml.sheet;base64,{link}">📥 Download Results as an excel file</a>'))
            display(HTML(filt.to_html(index=False)))

submit_btn.on_click(show_results)

# --------------------------
# Displaying the basic UI
# --------------------------

display(
    banner,
    note_html,
    jee_main_input, jee_adv_input,
    year_dropdown, round_dropdown,
    inst_dropdown, gender_dropdown, seat_dropdown,
    course_duration,
    widgets.HBox([advanced_btn, refresh_btn]),
    adv_box,
    submit_btn,
    output_area
)

HTML(value='\n    <div style="text-align:center; margin-bottom:10px;">\n      <img src="data:image/png;base64,…

HTML(value='<b>Note:</b> If you haven’t cleared JEE&nbsp;Mains or JEE&nbsp;Advanced, please enter the rank as …

IntText(value=1500000, description='JEE Mains:')

IntText(value=400000, description='JEE Adv:')

Dropdown(description='Year:', options=('2024', '2023', '2022', '2021', '2020'), value='2024')

...

Dropdown(description='Gender:', options=('Gender-Neutral', 'Female-only (including Supernumerary)'), value='Ge…

Dropdown(description='Seat Type:', options=('OPEN', 'EWS', 'OBC-NCL', 'SC', 'ST', 'OPEN (PwD)', 'OBC-NCL (PwD)…

ToggleButtons(description='Duration:', index=2, options=('4-Year', '5-Year', 'Both'), value='Both')

Button(button_style='success', description='Show Results', style=ButtonStyle())

Output()